In [1]:
import pandas as pd
from IPython.display import display, HTML
from ydata_profiling import ProfileReport
import json

### Load the dataset

In [2]:
filename = "customers_generated_100000_seed42.jsonl"
with open(filename) as f:
    records = [json.loads(line) for line in f]

### Normalise the data

In [3]:
import uuid

# Imagine these tables are dimentional tables in a database
# We will normalize the data into separate lists for customers, orders, payments, and transactions
customers = []
orders = []
payments = []
transactions = []

for row in records:
    cust = row['customer'].copy()
    cust['fraudulent'] = row['fraudulent']
    customers.append(cust)

    # Generate a deterministic customerId based on the customer email
    cust['customerId'] = str(uuid.uuid5(uuid.NAMESPACE_DNS, cust['customerEmail']))

 
    # We will add customerId to each of these objects to maintain the relationship. 
    # The ** operator is used to unpack the dictionary into key-value pairs

    for order in row.get('orders', []):
        orders.append({**order, "customerId": cust['customerId']})

    for payment in row.get('paymentMethods', []):
        payments.append({**payment, "customerId": cust['customerId']})

    for transaction in row.get('transactions', []):
        transactions.append({**transaction, "customerId": cust['customerId']})


### Convert the lists into pandas dataframes

In [4]:
df_customers = pd.DataFrame(customers)
df_orders = pd.DataFrame(orders)
df_payments = pd.DataFrame(payments)
df_transactions = pd.DataFrame(transactions)

### Convert the datetime logs to datetime

In [5]:
df_customers['loggedAt'] = pd.to_datetime(df_customers['loggedAt'])
df_orders['loggedAt'] = pd.to_datetime(df_orders['loggedAt'])
df_payments['loggedAt'] = pd.to_datetime(df_payments['loggedAt'])       
df_transactions['loggedAt'] = pd.to_datetime(df_transactions['loggedAt'])


### Add a is_succes flag to the transactions dataframe

In [6]:
# The ~ operator is used to invert a boolean Series in pandas.
# Here, it converts False to True
df_transactions['isTransactionSuccessful'] = (~df_transactions['transactionFailed']).astype(int)


### Generate derived features

In [7]:
# df_transactions = df_transactions.sort_values(['customerId', 'loggedAt'])

# # Set index and rolling count
# df_transactions = df_transactions.set_index('loggedAt')
# df_transactions['noTxnsInLast24h'] = (
#     df_transactions
#     .groupby('customerId')
#     .rolling('24h').transactionId.count()
#     .reset_index(level=0, drop=True)
# )

In [8]:
df_transactions_payments = df_transactions.merge(
    df_payments[['paymentMethodId', 'paymentMethodIssuer']],
    on='paymentMethodId',
    how='left'
)

df_transactions_payments = df_transactions_payments.sort_values(['paymentMethodIssuer', 'loggedAt'])
df_transactions_payments = df_transactions_payments.set_index('loggedAt')

df_transactions_payments['txnsIn24hByIssuer'] = (
    df_transactions_payments
    .groupby('paymentMethodIssuer')
    .rolling('24h').transactionId.count()
    .reset_index(level=0, drop=True)
)

df_transactions_payments['sucessfulTxnsIn24hByIssuer'] = (
    df_transactions_payments
    .groupby('paymentMethodIssuer')
    .rolling('24h')['isTransactionSuccessful']
    .sum()
    .reset_index(level=0, drop=True)
)

df_transactions_payments['txnsIn24hByIssuer'] = df_transactions_payments['txnsIn24hByIssuer'].fillna(0)
df_transactions_payments['sucessfulTxnsIn24hByIssuer'] = df_transactions_payments['sucessfulTxnsIn24hByIssuer'].fillna(0)

In [9]:
df_transactions = df_transactions.merge(
    df_transactions_payments[['transactionId', 'txnsIn24hByIssuer', 'sucessfulTxnsIn24hByIssuer']],
    on='transactionId',
    how='left'
)

del df_transactions_payments

### Additional derived features. 

- **Customer-level aggregates:** Lifetime value, average order size, recency, frequency, depravation index, etc.
- **Transaction/order patterns:** Unusual time-of-day, volume spikes, new shipping addresses, no of devices, no of IPAddresses
- **Payment features:** Payment method usage patterns, failed payment attempts, no of payment methods, etc.
- **Location-based risk:** Distance between billing/shipping, country risk score, Shipping Address + IP Address Mismatch

### Merge indivual dataframes into one single dataframe for feature engineering

In [10]:
df = (
    df_transactions
    .merge(df_orders, on=['orderId', 'customerId'], how='left', suffixes=('', '_order'))
    .merge(df_payments, left_on=['paymentMethodId', 'customerId'], right_on=['paymentMethodId', 'customerId'], how='left', suffixes=('', '_payment'))
    .merge(df_customers, on='customerId', how='left', suffixes=('', '_customer'))
)

### Exploratory data analysis (EDA) 

In [11]:
profile = ProfileReport(df, title="EDA Profiling Report", explorative=True)

In [12]:
profile.to_notebook_iframe()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 26/26 [00:15<00:00,  1.71it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Export clean data

In [13]:
df.to_csv('data/clean.csv', index=False)